## Set up data frames

- Set up new repo: pscyhopy_video_extract
- Added in data folder with pid 0601 to test with
- Set up Jupyter notebook to probe data
- Read in psychopy data
- Remove rows that do not have ‘trial’ as display.
- Remove rows from block 2 (data not recorded :’( …)
- Using fixation start as timepoint, create a zeroed timestamp column. 
- Create 3 data frames for left/right/centre

In [11]:
import pandas as pd

# Set up data files and select block 1 data. 
wc_data = pd.read_csv('data/0601_webcam_data.csv')
wc_data['tstamp'] = wc_data['fix_start'] / 30
wc_tstamp = wc_data['tstamp'].values

psy_data = pd.read_csv('data/0601_mag_comparison_numeral_2023-02-06_16h57.47.462.csv')
psy_data = psy_data[(psy_data['display']=='trial')]

# Timestamp based on webcam frames
psy_data['wc_tstamp'] = wc_tstamp
psy_data = psy_data[(psy_data['target_duration_90'] == 0)] 

# Get first fixation timestamp to act as 0 value
zero_point = psy_data['fixation.started'].iloc[0]


#Create df for each orientation
left_time_psy_data = pd.DataFrame()
left_time_psy_data['fix_start'] = psy_data['fixation.started']
left_time_psy_data['synced_time'] = psy_data['fixation.started'] - zero_point
left_time_psy_data['frame_time'] = psy_data['wc_tstamp']
left_time_psy_data['roi_on'] = psy_data['roi_left.timesOn']
left_time_psy_data['roi_off'] = psy_data['roi_left.timesOff']


right_time_psy_data = pd.DataFrame()
right_time_psy_data['fix_start'] = psy_data['fixation.started']
right_time_psy_data['synced_time'] = psy_data['fixation.started'] - zero_point
right_time_psy_data['frame_time'] = psy_data['wc_tstamp']
right_time_psy_data['roi_on'] = psy_data['roi_right.timesOn']
right_time_psy_data['roi_off'] = psy_data['roi_right.timesOff']


centre_time_psy_data = pd.DataFrame()
centre_time_psy_data['fix_start'] = psy_data['fixation.started']
centre_time_psy_data['synced_time'] = psy_data['fixation.started'] - zero_point
centre_time_psy_data['frame_time'] = psy_data['wc_tstamp']
centre_time_psy_data['roi_on'] = psy_data['roi_centre.timesOn']
centre_time_psy_data['roi_off'] = psy_data['roi_centre.timesOff']



## Loop through data frames and get times

- loop through a data frame and access the data
- create variable of the on - off times 
- workout the timestamp for start stop from zeroed values



In [12]:

# creates empty output data frames
left_ET_output = pd.DataFrame({'trial':[], 'time_zero':[], 'ET_on':[], 'ET_off':[]})
right_ET_output = pd.DataFrame({'trial':[], 'time_zero':[], 'ET_on':[], 'ET_off':[]})
centre_ET_output = pd.DataFrame({'trial':[], 'time_zero':[], 'ET_on':[], 'ET_off':[]})


# 3 identical loops for each orientation
for i, row in left_time_psy_data.iterrows():

    #Checks if any ET activity
    if pd.notna(row['roi_on']):
        
        # Converts each ET time to a list and runs through
        for (ET_on, ET_off) in zip(eval(row['roi_on']), eval(row['roi_off'])):
            # create empty output 
            temp_output = pd.DataFrame({'trial':i, 'time_zero':row['frame_time'],'ET_on': row['frame_time'] + ET_on, 'ET_off': row['frame_time'] + ET_off}, index=[0])
            # concat temp and output 
            left_ET_output = pd.concat([left_ET_output,temp_output], ignore_index=True)


for i, row in right_time_psy_data.iterrows():

    if pd.notna(row['roi_on']):
        
        for (ET_on, ET_off) in zip(eval(row['roi_on']), eval(row['roi_off'])):
            temp_output = pd.DataFrame({'trial':i, 'time_zero':row['frame_time'],'ET_on': row['frame_time'] + ET_on, 'ET_off': row['frame_time'] + ET_off}, index=[0])
            right_ET_output = pd.concat([right_ET_output,temp_output], ignore_index=True)

for i, row in centre_time_psy_data.iterrows():

    if pd.notna(row['roi_on']):
        
        for (ET_on, ET_off) in zip(eval(row['roi_on']), eval(row['roi_off'])):
            temp_output = pd.DataFrame({'trial':i, 'time_zero':row['frame_time'],'ET_on': row['frame_time'] + ET_on, 'ET_off': row['frame_time'] + ET_off}, index=[0])
            centre_ET_output = pd.concat([centre_ET_output,temp_output], ignore_index=True)


          



In [14]:
import sys
import subprocess
sys.path.append('/Users/alexwork/Documents/Development/gazescorer/')
import GazeScorer as gs
import datetime
import ffmpeg

vfname = 'data/0601_trial_video.avi'


for i, vrow in left_ET_output.iterrows():
    
    output_fname = f'output/left/{i}_{int(vrow["trial"])}_L.mp4'
    ET_on = str(datetime.timedelta(seconds=vrow['ET_on']))
    ET_off = str(datetime.timedelta(seconds=vrow['ET_off']))


    command_video = f'ffmpeg -ss {ET_on} -to {ET_off} -i {vfname} -c copy {output_fname} -y'

    subprocess.run(command_video, shell=True)


for i, vrow in right_ET_output.iterrows():
    
    output_fname = f'output/right/{i}_{int(vrow["trial"])}_R.mp4'
    ET_on = str(datetime.timedelta(seconds=vrow['ET_on']))
    ET_off = str(datetime.timedelta(seconds=vrow['ET_off']))

    command_video = f'ffmpeg -ss {ET_on} -to {ET_off} -i {vfname} -c copy {output_fname} -y'

    subprocess.run(command_video, shell=True)

for i, vrow in centre_ET_output.iterrows():
    
    output_fname = f'output/centre/{i}_{int(vrow["trial"])}_C.mp4'
    ET_on = str(datetime.timedelta(seconds=vrow['ET_on']))
    ET_off = str(datetime.timedelta(seconds=vrow['ET_off']))

    command_video = f'ffmpeg -ss {ET_on} -to {ET_off} -i {vfname} -c copy {output_fname} -y'

    subprocess.run(command_video, shell=True)





    # gs.video_utils.preprocess_video(vfname,processed_fname=output_fname, overwrite_video=True, start_time=vrow['ET_on'], stop_time=vrow['ET_off'])


ffmpeg version 4.3.2 Copyright (c) 2000-2021 the FFmpeg developers
  built with clang version 11.1.0
  configuration: --prefix=/Users/alexwork/opt/miniconda3/envs/gazescorer --cc=x86_64-apple-darwin13.4.0-clang --disable-doc --disable-openssl --enable-avresample --enable-gnutls --enable-gpl --enable-hardcoded-tables --enable-libfreetype --enable-libopenh264 --enable-libx264 --enable-pic --enable-pthreads --enable-shared --enable-static --enable-version3 --enable-zlib --enable-libmp3lame --pkg-config=/Users/runner/miniforge3/conda-bld/ffmpeg_1634125724063/_build_env/bin/pkg-config
  libavutil      56. 51.100 / 56. 51.100
  libavcodec     58. 91.100 / 58. 91.100
  libavformat    58. 45.100 / 58. 45.100
  libavdevice    58. 10.100 / 58. 10.100
  libavfilter     7. 85.100 /  7. 85.100
  libavresample   4.  0.  0 /  4.  0.  0
  libswscale      5.  7.100 /  5.  7.100
  libswresample   3.  7.100 /  3.  7.100
  libpostproc    55.  7.100 / 55.  7.100
Input #0, avi, from 'data/0601_trial_video.a

In [17]:
import pandas as pd



# Set up data files and select block 1 data. 
wc_data = pd.read_csv('data/0601_webcam_data.csv')
wc_data['tstamp'] = wc_data['fix_start'] / 30
wc_tstamp = wc_data['tstamp'].values

psy_data = pd.read_csv('data/0601_mag_comparison_numeral_2023-02-06_16h57.47.462.csv')
psy_data = psy_data[(psy_data['display']=='trial')]

# Timestamp based on webcam frames
psy_data['wc_tstamp'] = wc_tstamp
psy_data = psy_data[(psy_data['target_duration_90'] == 0)] 

# Get first fixation timestamp to act as 0 value
zero_point = psy_data['fixation.started'].iloc[0]


#Create df for each orientation
left_time_psy_data = pd.DataFrame()
left_time_psy_data['fix_start'] = psy_data['fixation.started']
left_time_psy_data['synced_time'] = psy_data['fixation.started'] - zero_point
left_time_psy_data['frame_time'] = psy_data['wc_tstamp']
left_time_psy_data['roi_on'] = psy_data['roi_left.timesOn']
left_time_psy_data['roi_off'] = psy_data['roi_left.timesOff']


right_time_psy_data = pd.DataFrame()
right_time_psy_data['fix_start'] = psy_data['fixation.started']
right_time_psy_data['synced_time'] = psy_data['fixation.started'] - zero_point
right_time_psy_data['frame_time'] = psy_data['wc_tstamp']
right_time_psy_data['roi_on'] = psy_data['roi_right.timesOn']
right_time_psy_data['roi_off'] = psy_data['roi_right.timesOff']


centre_time_psy_data = pd.DataFrame()
centre_time_psy_data['fix_start'] = psy_data['fixation.started']
centre_time_psy_data['synced_time'] = psy_data['fixation.started'] - zero_point
centre_time_psy_data['frame_time'] = psy_data['wc_tstamp']
centre_time_psy_data['roi_on'] = psy_data['roi_centre.timesOn']
centre_time_psy_data['roi_off'] = psy_data['roi_centre.timesOff']




In [6]:
import glob
import pandas as pd
import subprocess
import datetime


files = glob.glob('data/*.avi')

for f in files:

    pid = f.replace('_trial_video.avi',"")
    pid = pid.replace('data/',"")



    # Set up data files and select block 1 data. 
    wc_data = pd.read_csv(f'data/{pid}_webcam_data.csv')
    wc_data['tstamp'] = wc_data['fix_start'] / 30  
    wc_tstamp = wc_data['tstamp'].values

    psy_data = pd.read_csv(f'data/{pid}_mag_comparison_numeral.csv')
    psy_data = psy_data[(psy_data['display']=='trial')]

    # Timestamp based on webcam frames
    psy_data['wc_tstamp'] = wc_tstamp
    psy_data = psy_data[(psy_data['target_duration_90'] == 0)] 

    # Get first fixation timestamp to act as 0 value
    zero_point = psy_data['fixation.started'].iloc[0]


    #Create df for each orientation
    left_time_psy_data = pd.DataFrame()
    left_time_psy_data['fix_start'] = psy_data['fixation.started']
    left_time_psy_data['synced_time'] = psy_data['fixation.started'] - zero_point
    left_time_psy_data['frame_time'] = psy_data['wc_tstamp']
    left_time_psy_data['roi_on'] = psy_data['roi_left.timesOn']
    left_time_psy_data['roi_off'] = psy_data['roi_left.timesOff']


    right_time_psy_data = pd.DataFrame()
    right_time_psy_data['fix_start'] = psy_data['fixation.started']
    right_time_psy_data['synced_time'] = psy_data['fixation.started'] - zero_point
    right_time_psy_data['frame_time'] = psy_data['wc_tstamp']
    right_time_psy_data['roi_on'] = psy_data['roi_right.timesOn']
    right_time_psy_data['roi_off'] = psy_data['roi_right.timesOff']


    centre_time_psy_data = pd.DataFrame()
    centre_time_psy_data['fix_start'] = psy_data['fixation.started']
    centre_time_psy_data['synced_time'] = psy_data['fixation.started'] - zero_point
    centre_time_psy_data['frame_time'] = psy_data['wc_tstamp']
    centre_time_psy_data['roi_on'] = psy_data['roi_centre.timesOn']
    centre_time_psy_data['roi_off'] = psy_data['roi_centre.timesOff']


    # creates empty output data frames
    left_ET_output = pd.DataFrame({'trial':[], 'time_zero':[], 'ET_on':[], 'ET_off':[]})
    right_ET_output = pd.DataFrame({'trial':[], 'time_zero':[], 'ET_on':[], 'ET_off':[]})
    centre_ET_output = pd.DataFrame({'trial':[], 'time_zero':[], 'ET_on':[], 'ET_off':[]})


    # 3 identical loops for each orientation
    for i, row in left_time_psy_data.iterrows():

        #Checks if any ET activity
        if pd.notna(row['roi_on']):
            
            # Converts each ET time to a list and runs through
            for (ET_on, ET_off) in zip(eval(row['roi_on']), eval(row['roi_off'])):
                # create empty output 
                temp_output = pd.DataFrame({'trial':i, 'time_zero':row['frame_time'],'ET_on': row['frame_time'] + ET_on, 'ET_off': row['frame_time'] + ET_off}, index=[0])
                # concat temp and output 
                left_ET_output = pd.concat([left_ET_output,temp_output], ignore_index=True)


    for i, row in right_time_psy_data.iterrows():

        if pd.notna(row['roi_on']):
            
            for (ET_on, ET_off) in zip(eval(row['roi_on']), eval(row['roi_off'])):
                temp_output = pd.DataFrame({'trial':i, 'time_zero':row['frame_time'],'ET_on': row['frame_time'] + ET_on, 'ET_off': row['frame_time'] + ET_off}, index=[0])
                right_ET_output = pd.concat([right_ET_output,temp_output], ignore_index=True)

    for i, row in centre_time_psy_data.iterrows():

        if pd.notna(row['roi_on']):
            
            for (ET_on, ET_off) in zip(eval(row['roi_on']), eval(row['roi_off'])):
                temp_output = pd.DataFrame({'trial':i, 'time_zero':row['frame_time'],'ET_on': row['frame_time'] + ET_on, 'ET_off': row['frame_time'] + ET_off}, index=[0])
                centre_ET_output = pd.concat([centre_ET_output,temp_output], ignore_index=True)


    vfname = f'{f}'

    try:
        for i, vrow in left_ET_output.iterrows():
            
            output_fname = f'output/left/{pid}_{i}_{int(vrow["trial"])}_L.mp4'
            ET_on = str(datetime.timedelta(seconds=vrow['ET_on']))
            ET_off = str(datetime.timedelta(seconds=vrow['ET_off']))


            command_video = f'ffmpeg -ss {ET_on} -to {ET_off} -i {vfname} -c copy {output_fname} -y'

            subprocess.run(command_video, shell=True)


        for i, vrow in right_ET_output.iterrows():
            
            output_fname = f'output/right/{pid}_{i}_{int(vrow["trial"])}_R.mp4'
            ET_on = str(datetime.timedelta(seconds=vrow['ET_on']))
            ET_off = str(datetime.timedelta(seconds=vrow['ET_off']))

            command_video = f'ffmpeg -ss {ET_on} -to {ET_off} -i {vfname} -c copy {output_fname} -y'

            subprocess.run(command_video, shell=True)

        for i, vrow in centre_ET_output.iterrows():
            
            output_fname = f'output/centre/{pid}_{i}_{int(vrow["trial"])}_C.mp4'
            ET_on = str(datetime.timedelta(seconds=vrow['ET_on']))
            ET_off = str(datetime.timedelta(seconds=vrow['ET_off']))

            command_video = f'ffmpeg -ss {ET_on} -to {ET_off} -i {vfname} -c copy {output_fname} -y'

            subprocess.run(command_video, shell=True)

    except:

        print(f'{pid} failed...')


            


    



ffmpeg version 4.3.2 Copyright (c) 2000-2021 the FFmpeg developers
  built with clang version 11.1.0
  configuration: --prefix=/Users/alexwork/opt/miniconda3/envs/gazescorer --cc=x86_64-apple-darwin13.4.0-clang --disable-doc --disable-openssl --enable-avresample --enable-gnutls --enable-gpl --enable-hardcoded-tables --enable-libfreetype --enable-libopenh264 --enable-libx264 --enable-pic --enable-pthreads --enable-shared --enable-static --enable-version3 --enable-zlib --enable-libmp3lame --pkg-config=/Users/runner/miniforge3/conda-bld/ffmpeg_1634125724063/_build_env/bin/pkg-config
  libavutil      56. 51.100 / 56. 51.100
  libavcodec     58. 91.100 / 58. 91.100
  libavformat    58. 45.100 / 58. 45.100
  libavdevice    58. 10.100 / 58. 10.100
  libavfilter     7. 85.100 /  7. 85.100
  libavresample   4.  0.  0 /  4.  0.  0
  libswscale      5.  7.100 /  5.  7.100
  libswresample   3.  7.100 /  3.  7.100
  libpostproc    55.  7.100 / 55.  7.100
Input #0, avi, from 'data/0005_trial_video.a